In [1]:
import pandas as pd
import numpy as np
import os
import sumolib
import random
from tqdm import tqdm
from datetime import datetime

# A. 이동류 매칭

In [2]:
# [이동류번호] 불러오기 (약 1분의 소요시간)
path_moves = '../../Data/tables/moves/'
csv_moves = os.listdir('../../Data/tables/moves/')
moves = [pd.read_csv(path_moves + csv_move, index_col=0) for csv_move in tqdm(csv_moves)]
match1 = pd.concat(moves).drop_duplicates().sort_values(by=['inter_no','phas_A','phas_B']).reset_index(drop=True)
match1.head(10)

100%|██████████| 17280/17280 [00:58<00:00, 294.84it/s]


inter_no  phas_A  phas_B  move_A  move_B
0       175       1       1       8       4
1       175       2       2       7       3
2       175       3       3       6       1
3       175       3       4       6       2
4       175       4       4       5       2
5       176       1       1       8       4
6       176       2       2       8       3
7       176       3       3       5      18
8       177       1       1       8       4
9       177       2       2       7       3

In [3]:
# 계층화 (inter_no, phas_A, phas_B, move_A, move_B) -> ('inter_no', 'phase_no', 'ring_type', 'move_no')
matchA = match1[['inter_no', 'phas_A', 'move_A']].copy()
matchA.columns = ['inter_no', 'phase_no', 'move_no']
matchA['ring_type'] = 'A'
matchB = match1[['inter_no', 'phas_B', 'move_B']].copy()
matchB.columns = ['inter_no', 'phase_no', 'move_no']
matchB['ring_type'] = 'B'
match2 = pd.concat([matchA, matchB]).drop_duplicates()
match2 = match2[['inter_no', 'phase_no', 'ring_type', 'move_no']]
match2 = match2.sort_values(by=list(match2.columns))
match2.head(10)

inter_no  phase_no ring_type  move_no
0       175         1         A        8
0       175         1         B        4
1       175         2         A        7
1       175         2         B        3
2       175         3         A        6
2       175         3         B        1
4       175         4         A        5
3       175         4         B        2
5       176         1         A        8
5       176         1         B        4

In [4]:
# [nema 이동류목록] 불러오기 및 병합
nema = pd.read_csv('../../Data/tables/nema.csv', encoding='cp949')
match3 = pd.merge(match2, nema, how='left', on='move_no').drop_duplicates()
match3

inter_no  phase_no ring_type  move_no inc_dir out_dir
0        175         1         A        8       남       북
1        175         1         B        4       북       남
2        175         2         A        7       북       동
3        175         2         B        3       남       서
4        175         3         A        6       동       서
..       ...       ...       ...      ...     ...     ...
59       210         4         B        3       남       서
60       211         1         A        6       동       서
61       211         1         B        2       서       동
62       211         2         A       17     NaN     NaN
63       211         2         B       18     NaN     NaN

[64 rows x 6 columns]

In [5]:
# [방위각정보] 불러오기, 계층화, 병합
# 불러오기
dtype_dict = {f'angle_{alph}{j}':'str' for alph in ['A', 'B'] for j in range(1,9)}
angle_original = pd.read_csv('../../Data/tables/angle.csv', index_col=0, dtype = dtype_dict)
# 계층화
angle = []
for i, row in angle_original.iterrows():
    angle_codes = row[[f'angle_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]]
    new = pd.DataFrame({'inter_no':[row.inter_no] * 16, 'phase_no':list(range(1, 9))*2, 'ring_type':['A'] * 8 + ['B'] * 8, 'angle_code':angle_codes.to_list()})
    angle.append(new)
angle = pd.concat(angle)
angle = angle.dropna().reset_index(drop=True)
# 병합
six_chars = angle.angle_code.apply(lambda x:len(x)==6)
angle.loc[six_chars,'inc_angle'] = angle.angle_code.apply(lambda x:x[:3])
angle.loc[six_chars,'out_angle'] = angle.angle_code.apply(lambda x:x[3:])
angle = angle.drop('angle_code', axis=1)
match4 = pd.merge(match3, angle, how='left', left_on=['inter_no', 'phase_no', 'ring_type'],
                 right_on=['inter_no', 'phase_no', 'ring_type']).drop_duplicates()
match4

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle
0        175         1         A        8       남       북       179       004
1        175         1         B        4       북       남       003       176
2        175         2         A        7       북       동       001       095
3        175         2         B        3       남       서       179       270
4        175         3         A        6       동       서       090       270
..       ...       ...       ...      ...     ...     ...       ...       ...
59       210         4         B        3       남       서       180       270
60       211         1         A        6       동       서       090       270
61       211         1         B        2       서       동       270       090
62       211         2         A       17     NaN     NaN       NaN       NaN
63       211         2         B       18     NaN     NaN       NaN       NaN

[64 rows x 8 columns]

In [6]:
# [네트워크], [교차로-노드 매칭], [교차로정보] 불러오기 
net = sumolib.net.readNet('../../Data/networks/SN_sample.net.xml')
inter_node = pd.read_csv('../../Data/tables/inter_node.csv', index_col=0)
inter_info = pd.read_csv('../../Data/tables/inter_info.csv', index_col=0)

inter_node1 = inter_node[inter_node.inter_type == 'parent'].drop('inter_type', axis=1)
inter_info1 = inter_info[['inter_no', 'inter_lat', 'inter_lon']]
inter = pd.merge(inter_node1, inter_info1, how='left', left_on=['inter_no'],
                 right_on=['inter_no']).drop_duplicates()

inter2node = dict(zip(inter['inter_no'], inter['node_id']))

match5 = match4.copy()
# 진입진출ID 매칭
for index, row in match5.iterrows():
    node_id = inter2node[row.inter_no]
    node = net.getNode(node_id)
    # 교차로의 모든 (from / to) edges
    inc_edges = [edge for edge in node.getIncoming() if edge.getFunction() == ''] # incoming edges
    out_edges = [edge for edge in node.getOutgoing() if edge.getFunction() == ''] # outgoing edges
    # 교차로의 모든 (from / to) directions
    inc_dirs = []
    for inc_edge in inc_edges:
        start = inc_edge.getShape()[-2]
        end = inc_edge.getShape()[-1]
        inc_dir = np.array(end) - np.array(start)
        inc_dir = inc_dir / (inc_dir ** 2).sum() ** 0.5
        inc_dirs.append(inc_dir)
    out_dirs = []
    for out_edge in out_edges:
        start = out_edge.getShape()[0]
        end = out_edge.getShape()[1]
        out_dir = np.array(end) - np.array(start)
        out_dir = out_dir / (out_dir ** 2).sum() ** 0.5
        out_dirs.append(out_dir)
    # 진입각, 진출각 불러오기
    if not pd.isna(row.inc_angle):
        inc_angle = int(row.inc_angle)
        out_angle = int(row.out_angle)
        # 방위각을 일반각으로 가공, 라디안 변환, 단위벡터로 변환
        inc_angle = (-90 - inc_angle) % 360
        inc_angle = inc_angle * np.pi / 180.
        inc_dir_true = np.array([np.cos(inc_angle), np.sin(inc_angle)])
        out_angle = (90 - out_angle) % 360
        out_angle = out_angle * np.pi / 180.
        out_dir_true = np.array([np.cos(out_angle), np.sin(out_angle)])
        # 매칭 엣지 반환
        inc_index = np.array([np.dot(inc_dir, inc_dir_true) for inc_dir in inc_dirs]).argmax()
        out_index = np.array([np.dot(out_dir, out_dir_true) for out_dir in out_dirs]).argmax()
        inc_edge_id = inc_edges[inc_index].getID()
        out_edge_id   = out_edges[out_index].getID()
        match5.at[index, 'inc_edge'] = inc_edge_id
        match5.at[index, 'out_edge'] = out_edge_id
match5['node_id'] = match5['inter_no'].map(inter2node)
# match5 = match5[['inter_no', 'node_id', 'move_no', 'inc_edge', 'out_edge']]
match5 = match5.sort_values(by=['inter_no', 'move_no']).reset_index(drop=True)

In [7]:
# 이동류 매칭
# 각 교차로에 대하여, 가능한 모든 이동류(1~18, 21)에 대한 진입·진출엣지ID를 지정한다.
# 모든 이동류에 대해 지정하므로, 시차제시 이전과 다른 이동류가 등장하더라도 항상 진입·진출 엣지 ID를 지정할 수 있다.
match6 = match5.copy().dropna()
match6 = match6[['inter_no', 'move_no', 'inc_dir', 'out_dir', 'inc_edge', 'out_edge', 'node_id']]
# (1) 가능한 (진입방향, 진출방향) 목록
flows = nema.dropna().apply(lambda row: (row['inc_dir'], row['out_dir']), axis=1).tolist()
# (2) 각 교차로별 방향 목록 : pdires
pdires = {}
for inter_no in match6.inter_no.unique():
    dires = match6[match6.inter_no == inter_no][['inc_dir','out_dir']].values.flatten()
    dires = {dire for dire in dires if type(dire)==str}
    pdires[inter_no] = dires
# (3) 각 (교차로, 진입방향) 별 진입id 목록 : inc2id
inc2id = {}
for inter_no in match6.inter_no.unique():
    for inc_dir in pdires[inter_no]:
        df = match6[(match6.inter_no==inter_no) & (match6.inc_dir==inc_dir)]
        inc2id[(inter_no, inc_dir)] = df.inc_edge.iloc[0]
# (4) 각 (교차로, 진출방향) 별 진출id 목록 : out2id
out2id = {}
for inter_no in match6.inter_no.unique():
    for out_dir in pdires[inter_no]:
        df = match6[(match6.inter_no==inter_no) & (match6.out_dir==out_dir)]
        out2id[(inter_no, out_dir)] = df.out_edge.iloc[0]
# (5) 각 교차로별 가능한 (진입방향, 진출방향) 목록 : pflows
pflow = {}
for inter_no in match6.inter_no.unique():
    pflow[inter_no] = [flow for flow in flows if set(flow).issubset(pdires[inter_no])]
# (6) 가능한 이동류에 대하여 진입id, 진출id 배정 : matching
inter2node = dict(zip(match6['inter_no'], match6['node_id']))
dires_right = ['북', '서', '남', '동', '북']
matching = []
for inter_no in match6.inter_no.unique():
    node_id = inter2node[inter_no]
    # 좌회전과 직진(1 ~ 16)
    for (inc_dir, out_dir) in pflow[inter_no]:
        move_no = nema[(nema.inc_dir==inc_dir) & (nema.out_dir==out_dir)].move_no.iloc[0]
        inc_edge = inc2id[(inter_no, inc_dir)]
        out_edge = out2id[(inter_no, out_dir)]
        new_row = pd.DataFrame({'inter_no':[inter_no], 'move_no':[move_no],
                                'inc_dir':[inc_dir], 'out_dir':[out_dir],
                                'inc_edge':[inc_edge], 'out_edge':[out_edge], 'node_id':[node_id]})
        matching.append(new_row)
    # 보행신호(17), 전적색(18)
    new_row = pd.DataFrame({'inter_no':[inter_no] * 2, 'move_no':[17, 18],
                            'inc_dir':[None]*2, 'out_dir':[None]*2,
                            'inc_edge':[None]*2, 'out_edge':[None]*2, 'node_id':[node_id]*2})
    matching.append(new_row)
    # 신호우회전(21)
    for d in range(len(dires_right)-1):
        inc_dir = dires_right[d]
        out_dir = dires_right[d+1]
        if {inc_dir, out_dir}.issubset(pdires[inter_no]):
            inc_edge = inc2id[(inter_no, inc_dir)]
            out_edge = out2id[(inter_no, out_dir)]
            new_row = pd.DataFrame({'inter_no':[inter_no], 'move_no':[21],
                                    'inc_dir':[inc_dir], 'out_dir':[out_dir],
                                    'inc_edge':[inc_edge], 'out_edge':[out_edge], 'node_id':[node_id]})
            matching.append(new_row)
matching = pd.concat(matching)
matching = matching.sort_values(by=['inter_no', 'move_no']).reset_index(drop=True)
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    display(matching)

inter_no  move_no inc_dir out_dir          inc_edge          out_edge  \
0        175        1       동       남      571545870_02      571542797_02   
1        175        2       서       동      571510153_02      571545870_01   
2        175        3       남       서     -571542797_02      571510153_01   
3        175        4       북       남     -571500487_01      571542797_02   
4        175        5       서       북      571510153_02      571500487_01   
5        175        6       동       서      571545870_02      571510153_01   
6        175        7       북       동     -571500487_01      571545870_01   
7        175        8       남       북     -571542797_02      571500487_01   
8        175       17    None    None              None              None   
9        175       18    None    None              None              None   
10       175       21       북       서     -571500487_01      571510153_01   
11       175       21       서       남      571510153_02      571542797_02   
12       175       21       남       동     -571542797_02      571545870_01   
13       175       21       동       북      571545870_02      571500487_01   
14       176        3       남       서     -571542810_01      571543469_01   
15       176        4       북       남   571542797_02.99      571542810_01   
16       176        5       서       북      571543469_02  -571542797_02.99   
17       176        8       남       북     -571542810_01  -571542797_02.99   
18       176       17    None    None              None              None   
19       176       18    None    None              None              None   
20       176       21       북       서   571542797_02.99      571543469_01   
21       176       21       서       남      571543469_02      571542810_01   
22       177        1       동       남      571542107_02      571542809_01   
23       177        2       서       동     -571542809_01      571542107_01   
24       177        3       남       서     -571542809_01      571542809_01   
25       177        4       북       남      571542811_02      571542809_01   
26       177        5       서       북     -571542809_01      571542811_01   
27       177        6       동       서      571542107_02      571542809_01   
28       177        7       북       동      571542811_02      571542107_01   
29       177        8       남       북     -571542809_01      571542811_01   
30       177       17    None    None              None              None   
31       177       18    None    None              None              None   
32       177       21       북       서      571542811_02      571542809_01   
33       177       21       서       남     -571542809_01      571542809_01   
34       177       21       남       동     -571542809_01      571542107_01   
35       177       21       동       북      571542107_02      571542811_01   
36       178        1       동       남     -571500475_01      571540304_01   
37       178        2       서       동   571540303_02.21      571500475_01   
38       178        3       남       서      571540304_02      571540303_01   
39       178        4       북       남      571556450_02      571540304_01   
40       178        5       서       북   571540303_02.21      571556450_01   
41       178        6       동       서     -571500475_01      571540303_01   
42       178        7       북       동      571556450_02      571500475_01   
43       178        8       남       북      571540304_02      571556450_01   
44       178       17    None    None              None              None   
45       178       18    None    None              None              None   
46       178       21       북       서      571556450_02      571540303_01   
47       178       21       서       남   571540303_02.21      571540304_01   
48       178       21       남       동      571540304_02      571500475_01   
49       178       21       동       북     -571500475_01      571556450_01   
50       201        1       동       남      571500617_02      571500569_01   


# B. 5초 간격으로 이동류번호 수집

In [8]:
# 5초 단위로 이동류번호 저장 및 신호이력에서 유닉스시각 가져와서 표시, 한시간동안의 데이터만 보관
midnight = int(datetime(2024, 1, 5, 0, 0, 0).timestamp())
next_day = int(datetime(2024, 1, 6, 0, 0, 0).timestamp())
fsecs = range(midnight, next_day, 5) # fsecs : unix time by Five SECondS
time2move = dict(zip(fsecs,moves)) # move : 어느 순간의 이동류정보
history = pd.read_csv('../../Data/tables/history.csv', index_col=0)

time2movement = {} # movement : 어느 순간의, 그 순간으로부터 한시간 동안의 (교차로번호 + 현시별이동류번호 + 시작시간)
# - 아래 절차를 5초마다 반복
for fsec in tqdm(fsecs): # fsec : unix time by Five SECond
    # 1. 상태 테이블 조회해서 전체 데이터중 필요데이터(교차로번호, A링 현시번호, A링 이동류번호, B링 현시번호, B링 이동류번호)만 수집 : A
    move = time2move[fsec]
    # 2. 이력 테이블 조회해서 교차로별로 유닉스시간 최대인 데이터(교차로변호, 종료유닉스타임)만 수집 : B
    recent_histories = [group.iloc[-1:] for _, group in history[history['end_unix'] < fsec].groupby('inter_no')] # 교차로별로 유닉스시간이 최대인 행들
    if not recent_histories:
        rhistory = pd.DataFrame({'inter_no':[], 'end_unix':[]}) # recent history
    else:
        rhistory = pd.concat(recent_histories)
    recent_unix = rhistory[['inter_no', 'end_unix']]
    # 3. 상태 테이블 조회정보(A)와 이력 테이블 조회정보(B) 조인(키값 : 교차로번호) : C
    move = pd.merge(move, recent_unix, how='left', on='inter_no')
    move['end_unix'] = move['end_unix'].fillna(0).astype(int)
    move = move.drop_duplicates()
    # 4. C데이터 프레임에 신규 컬럼(시작 유닉스타임) 생성 후 종료유닉스 타임 값 입력, 종료 유닉스 타임 컬럼 제거
    move = move.rename(columns = {'end_unix':'start_unix'})
    # 5. 이동류 이력정보 READ
    #     - CSV 파일로 서버에 저장된 이동류정보를 읽어옴(파일이 없는 경우에는 데이터가 없는 프레임 D 생성)
    try:
        if isinstance(movement, pd.DataFrame): # movement가 존재할 경우 그걸 그대로 씀.
            pass
        else: 
            movement = pd.DataFrame()
    except NameError: # movement가 존재하지 않는 경우 생성
        movement = pd.DataFrame()
    # 6. 이동류 이력정보 데이터테이블(D)에 C데이터 add
    movement = pd.concat([movement, move])
    # 7. D데이터 프레임에서 중복데이터 제거(교차로번호, 시작 유닉스타임, A링 현시번호, B링 현시번호 같은 행은 제거)
    movement = movement.drop_duplicates(['inter_no','phas_A','phas_B','start_unix'])
    # 8. D데이터 보관 시간 기준시간을 시작 유닉스 타임의 최대값 - 3600을 값으로 산출하고, 보관 시간 기준시간보다 작은 시작 유닉스 타임을 가진 행은 모두 제거(1시간 데이터만 보관)
    movement = movement[movement.start_unix > fsec - 3600]
    start_unix_min = movement.start_unix.min()
    start_unix_max = movement.start_unix.max()
    movement = movement.sort_values(by=['start_unix','inter_no','phas_A','phas_B']).reset_index(drop=True)

    time2movement[fsec] = movement
    movement.to_csv(f'../../Data/tables/movements/movements_{fsec}.csv')

# 각 movement들의 길이 시각화
import matplotlib.pyplot as plt
plt.plot(fsecs, [len(time2movement[fsec]) for fsec in fsecs])
plt.close()

100%|██████████| 17280/17280 [02:00<00:00, 143.08it/s]


# C. 5분 간격으로 신호이력 수집 및 통합테이블 생성

In [267]:
pland = pd.read_csv('../../Data/tables/pland.csv', index_col=0)
plan = pd.read_csv('../../Data/tables/plan.csv', index_col=0)
history = pd.read_csv('../../Data/tables/history.csv', index_col=0)
display(pland.head())
display(history.head())
# plan은 A, B가 통합된 형식으로 history는 분리된 형식으로 표시되었음.

inter_no  start_hour  start_minute  ddur_1  ddur_2  ddur_3  ddur_4  ddur_5  \
0       175           0             0      37      39      25      30      29   
1       175           7             0      40      42      29      26      33   
2       175           9             0      43      45      33      22      37   
3       175          18            30      46      48      37      18      41   
4       176           0             0      37      73      40       0       0   

   ddur_6  ddur_7  ddur_8  cycle  offset  
0       0       0       0    160      57  
1       0       0       0    170      40  
2       0       0       0    180      28  
3       0       0       0    190      18  
4       0       0       0    150     131

inter_no    end_unix  ddur_1  ddur_2  ddur_3  ddur_4  ddur_5  ddur_6  \
0       206  1704380520      33      35      26      26       0       0   
1       211  1704380525      28      97       0       0       0       0   
2       178  1704380540      38      39      40      23       0       0   
3       201  1704380540      24      24      17      58      17       0   
4       202  1704380540      39     101       0       0       0       0   

   ddur_7  ddur_8  cycle  offset  
0       0       0    120      10  
1       0       0    125      45  
2       0       0    140      50  
3       0       0    140     133  
4       0       0    140     103

In [268]:
hist = history.copy()
hist = hist[hist.inter_no==175]
hist['diff'] = hist['end_unix'].diff().fillna(0).astype(int)
hist[70:90]

inter_no    end_unix  ddur_1  ddur_2  ddur_3  ddur_4  ddur_5  ddur_6  \
723       175  1704391690      37      39      25      30      29       0   
732       175  1704391850      37      39      25      30      29       0   
741       175  1704392010      37      39      25      30      29       0   
755       175  1704392170      37      39      25      30      29       0   
764       175  1704392330      37      39      25      30      29       0   
773       175  1704392490      37      39      25      30      29       0   
784       175  1704392651      37      39      25      30      29       0   
793       175  1704392810      37      39      25      30      29       0   
802       175  1704392970      37      39      25      30      29       0   
813       175  1704393130      37      39      25      30      29       0   
825       175  1704393290      37      39      25      30      29       0   
834       175  1704393450      37      39      25      30      29       0   
846       175  1704393610      37      39      25      30      29       0   
856       175  1704393770      37      39      25      30      29       0   
865       175  1704393930      37      39      25      30      29       0   
876       175  1704394090      37      39      25      30      29       0   
886       175  1704394250      37      39      25      30      29       0   
898       175  1704394410      37      39      25      30      29       0   
909       175  1704394570      37      39      25      30      29       0   
918       175  1704394730      37      39      25      30      29       0   

     ddur_7  ddur_8  cycle  offset  diff  
723       0       0    160      57   160  
732       0       0    160      57   160  
741       0       0    160      57   160  
755       0       0    160      57   160  
764       0       0    160      57   160  
773       0       0    160      57   160  
784       0       0    160      57   161  
793       0       0    160      57   159  
802       0       0    160      57   160  
813       0       0    160      57   160  
825       0       0    160      57   160  
834       0       0    160      57   160  
846       0       0    160      57   160  
856       0       0    160      57   160  
865       0       0    160      57   160  
876       0       0    160      57   160  
886       0       0    160      57   160  
898       0       0    160      57   160  
909       0       0    160      57   160  
918       0       0    160      57   160

In [269]:
# split, isplit : A,B 분리 혹은 통합시 사용될 수 있는 딕셔너리
splits = {} # splits maps (inter_no, start_hour, start_minute) to split
for i, row in plan.iterrows():
    inter_no = row.inter_no
    start_hour = row.start_hour
    start_minute = row.start_minute
    cycle = row.cycle
    cums_A = row[[f'dura_A{j}' for j in range(1,9)]].cumsum()
    cums_B = row[[f'dura_B{j}' for j in range(1,9)]].cumsum()
    splits[(inter_no, start_hour, start_minute)] = {} # split maps (phas_A, phas_B) to k
    k = 0
    for t in range(cycle):
        new_phas_A = len(cums_A[cums_A < t]) + 1
        new_phas_B = len(cums_B[cums_B < t]) + 1
        if k == 0 or ((new_phas_A, new_phas_B) != (phas_A, phas_B)):
            k += 1
        phas_A = new_phas_A
        phas_B = new_phas_B
        splits[(inter_no, start_hour, start_minute)][(phas_A, phas_B)] = k

isplits = {} # the inverse of splits
for i in splits:
    isplits[i] = {splits[i][k]:k for k in splits[i]} # isplit maps k to (phas_A, phas_B)

# timetable
timetable = plan[['start_hour', 'start_minute']].drop_duplicates()
timetable['start_seconds'] = midnight + timetable['start_hour'] * 3600 + timetable['start_minute'] * 60
timetable

start_hour  start_minute  start_seconds
0           0             0     1704380400
1           7             0     1704405600
2           9             0     1704412800
3          18            30     1704447000

In [270]:
sorted(history.inter_no.unique())

[175, 176, 177, 178, 201, 202, 206, 210, 211]

In [271]:
# inter_no == 178, end_unix ==1704460864

In [295]:
fmins = range(midnight, next_day, 300) # fmins : unix time by Five MINuteS
m = 273 # ranges from 0 to 287, but 0 makes an error where 288 = 86400//300
present_time = fmins[m] # 현재시점
# - 5분마다 신호이력 데이터 수집해서 통합테이블 생성할때
# 1. 조회시점의 유닉스 타임을 기준으로 신호이력의 유닉스 타임이 2시간 이내인 데이터 수집
rhistory = history.copy() # recent history 1704393231
rhistory = rhistory[(rhistory.end_unix < present_time) & (rhistory.end_unix >= present_time - 7200)]
hours = np.array(range(midnight, next_day + 1, 3600))
rhist = rhistory.copy()[rhistory.inter_no == 178]
hist = history.copy()[history.inter_no == 178]
end_unixes = hist.end_unix.unique()
rhist_diff = rhist.copy()
rhist_diff['diff'] = rhist_diff['end_unix'].diff().fillna(0).astype(int)
display(rhist_diff) # 결측치 처리 전
rhist = rhist.reset_index(drop=True)
new_rows = []
# 1-1. 결측치 처리 : 인접한 두 end_unix의 차이가 계획된 주기의 두 배보다 크면 결측이 일어났다고 판단
for n in range(len(rhist) - 1):
    curr_unix = rhist.iloc[n].end_unix # current end_unix
    next_unix = rhist.iloc[n+1].end_unix # next end_unix
    cycle = rhist.iloc[n].cycle
    start_seconds = np.array(timetable.start_seconds)
    idx = (start_seconds <= curr_unix).sum() - 1
    start_hour = timetable.iloc[idx].start_hour
    start_minute = timetable.iloc[idx].start_minute
    if next_unix - curr_unix >= 2 * cycle:
        # 현재 unix를 계획된 주기만큼 늘려가면서 한 행씩 채워나간다.
        #(다음 unix와의 차이가 계획된 주기보다 작거나 같아질 때까지)
        while next_unix - curr_unix > cycle:
            curr_unix += cycle
            # print(curr_unix)
            prow = pland[(pland.inter_no==178) & (pland.start_hour==start_hour) & (pland.start_minute==start_minute)] # planned row
            prow = prow.drop(['start_hour', 'start_minute'], axis=1)
            prow['end_unix'] = curr_unix
            display(prow)
            new_rows.append(prow)

rhist = pd.concat([rhist] + new_rows).sort_values(['end_unix'])
rhist_diff = rhist.copy()
rhist_diff['diff'] = rhist_diff['end_unix'].diff().fillna(0).astype(int)
display(rhist_diff) # 결측치 처리 후
rhist = rhist.reset_index(drop=True)

inter_no    end_unix  ddur_1  ddur_2  ddur_3  ddur_4  ddur_5  ddur_6  \
4264       178  1704455140      38      39      44      36      23       0   
4273       178  1704455320      38      39      44      36      23       0   
4282       178  1704455500      38      39      44      36      23       0   
4291       178  1704455680      38      39      44      36      23       0   
4301       178  1704455860      38      39      44      36      23       0   
4310       178  1704456040      38      39      44      36      23       0   
4319       178  1704456220      38      39      44      36      23       0   
4330       178  1704456400      38      39      44      36      23       0   
4339       178  1704456580      38      39      44      36      23       0   
4348       178  1704456759      38      39      44      36      23       0   
4358       178  1704456940      38      39      44      36      23       0   
4366       178  1704457120      38      39      44      36      23       0   
4375       178  1704457300      38      39      44      36      23       0   
4384       178  1704457480      38      39      44      36      23       0   
4394       178  1704457660      38      39      44      36      23       0   
4403       178  1704457840      38      39      44      36      23       0   
4411       178  1704458020      38      39      44      36      23       0   
4420       178  1704458201      38      39      44      36      23       0   
4431       178  1704458380      38      39      44      36      23       0   
4441       178  1704458560      38      39      44      36      23       0   
4450       178  1704458740      38      39      44      36      23       0   
4460       178  1704458920      38      39      44      36      23       0   
4468       178  1704459100      38      39      44      36      23       0   
4477       178  1704459280      38      39      44      36      23       0   
4487       178  1704459460      38      39      44      36      23       0   
4497       178  1704459640      38      39      44      36      23       0   
4506       178  1704459820      38      39      44      36      23       0   
4516       178  1704460000      38      39      44      36      23       0   
4526       178  1704460180      38      39      44      36      23       0   
4533       178  1704460360      38      39      44      36      23       0   
4559       178  1704460864      38      39      44      36      23       0   
4569       178  1704461040      38      39      44      36      23       0   
4577       178  1704461219      38      39      44      36      23       0   
4586       178  1704461400      38      39      44      36      23       0   
4597       178  1704461579      38      39      44      36      23       0   
4606       178  1704461760      38      39      44      36      23       0   
4615       178  1704461939      38      39      44      36      23       0   
4625       178  1704462120      38      39      44      36      23       0   

      ddur_7  ddur_8  cycle  offset  diff  
4264       0       0    180      75     0  
4273       0       0    180      75   180  
4282       0       0    180      75   180  
4291       0       0    180      75   180  
4301       0       0    180      75   180  
4310       0       0    180      75   180  
4319       0       0    180      75   180  
4330       0       0    180      75   180  
4339       0       0    180      75   180  
4348       0       0    180      75   179  
4358       0       0    180      75   181  
4366       0       0    180      75   180  
4375       0       0    180      75   180  
4384       0       0    180      75   180  
4394       0       0    180      75   180  
4403       0       0    180      75   180  
4411       0       0    180      75   180  
4420       0       0    180      75   181  
4431       0       0    180      75   179  
4441       0       0    180      75   180  
4450       0       0    180      75   1

inter_no  ddur_1  ddur_2  ddur_3  ddur_4  ddur_5  ddur_6  ddur_7  ddur_8  \
15       178      38      39      44      36      23       0       0       0   

    cycle  offset    end_unix  
15    180      75  1704460540

inter_no  ddur_1  ddur_2  ddur_3  ddur_4  ddur_5  ddur_6  ddur_7  ddur_8  \
15       178      38      39      44      36      23       0       0       0   

    cycle  offset    end_unix  
15    180      75  1704460720

inter_no    end_unix  ddur_1  ddur_2  ddur_3  ddur_4  ddur_5  ddur_6  \
0        178  1704455140      38      39      44      36      23       0   
1        178  1704455320      38      39      44      36      23       0   
2        178  1704455500      38      39      44      36      23       0   
3        178  1704455680      38      39      44      36      23       0   
4        178  1704455860      38      39      44      36      23       0   
5        178  1704456040      38      39      44      36      23       0   
6        178  1704456220      38      39      44      36      23       0   
7        178  1704456400      38      39      44      36      23       0   
8        178  1704456580      38      39      44      36      23       0   
9        178  1704456759      38      39      44      36      23       0   
10       178  1704456940      38      39      44      36      23       0   
11       178  1704457120      38      39      44      36      23       0   
12       178  1704457300      38      39      44      36      23       0   
13       178  1704457480      38      39      44      36      23       0   
14       178  1704457660      38      39      44      36      23       0   
15       178  1704457840      38      39      44      36      23       0   
16       178  1704458020      38      39      44      36      23       0   
17       178  1704458201      38      39      44      36      23       0   
18       178  1704458380      38      39      44      36      23       0   
19       178  1704458560      38      39      44      36      23       0   
20       178  1704458740      38      39      44      36      23       0   
21       178  1704458920      38      39      44      36      23       0   
22       178  1704459100      38      39      44      36      23       0   
23       178  1704459280      38      39      44      36      23       0   
24       178  1704459460      38      39      44      36      23       0   
25       178  1704459640      38      39      44      36      23       0   
26       178  1704459820      38      39      44      36      23       0   
27       178  1704460000      38      39      44      36      23       0   
28       178  1704460180      38      39      44      36      23       0   
29       178  1704460360      38      39      44      36      23       0   
15       178  1704460540      38      39      44      36      23       0   
15       178  1704460720      38      39      44      36      23       0   
30       178  1704460864      38      39      44      36      23       0   
31       178  1704461040      38      39      44      36      23       0   
32       178  1704461219      38      39      44      36      23       0   
33       178  1704461400      38      39      44      36      23       0   
34       178  1704461579      38      39      44      36      23       0   
35       178  1704461760      38      39      44      36      23       0   
36       178  1704461939      38      39      44      36      23       0   
37       178  1704462120      38      39      44      36      23       0   

    ddur_7  ddur_8  cycle  offset  diff  
0        0       0    180      75     0  
1        0       0    180      75   180  
2        0       0    180      75   180  
3        0       0    180      75   180  
4        0       0    180      75   180  
5        0       0    180      75   180  
6        0       0    180      75   180  
7        0       0    180      75   180  
8        0       0    180      75   180  
9        0       0    180      75   179  
10       0       0    180      75   181  
11       0       0    180      75   180  
12       0       0    180      75   180  
13       0       0    180      75   180  
14       0       0    180      75   180  
15       0       0    180      75   180  
16       0       0    180      75   180  
17       0       0    180      75   181  
18       0       0    180      75   179  
19       0       0    180      75   180  
20   

In [294]:
Rhist = rhist.copy() # recent history 1704393231
Rhist = rhist[(rhist.end_unix < present_time) & (rhist.end_unix >= present_time - 1200)]
Rhist = Rhist.reset_index(drop=True)
Rhist_diff = Rhist.copy()
Rhist_diff['diff'] = Rhist_diff['end_unix'].diff().fillna(0).astype(int)
display(Rhist_diff)
for n in range(len(Rhist)-1):
    curr_unix = Rhist.iloc[n].end_unix # current end_unix
    next_unix = Rhist.iloc[n+1].end_unix # current end_unix
    cycle = rhist.iloc[n].cycle
    R_n = (next_unix - curr_unix) / cycle
    print(R_n)
    start_seconds = np.array(timetable.start_seconds)
    idx = (start_seconds <= curr_unix).sum() - 1
    start_hour = timetable.iloc[idx].start_hour
    start_minute = timetable.iloc[idx].start_minute
    print(curr_unix)
    ghour_lt_curr_unix = hours[hours < curr_unix].max() # the greatest hour less than curr_unix
    end_unixes_lt_ghour = np.sort(end_unixes[end_unixes < ghour_lt_curr_unix]) # end unixes less than ghour_lt_end_unix
    base_unix = end_unixes_lt_ghour[-5] # 기준유닉스 : curr_unix보다 작은 hour 중에서 가장 큰 값으로부터 다섯 번째로 작은 end_unix
    print(base_unix)
    # D_n : 시간차이
    D_n = curr_unix - base_unix
    print(D_n)
    ddurations = rhist[(rhist.end_unix > base_unix) & (rhist.end_unix <= curr_unix)][[f'ddur_{j}' for j in range(1,9)]]
    # S_n : 현시시간합
    S_n = ddurations.values.sum()
    print(S_n)
    print(D_n - S_n)
    if (abs(D_n - S_n) > 10) & (R_n > 0.5):
        prow = pland[(pland.inter_no==178) & (pland.start_hour==start_hour) & (pland.start_minute==start_minute)].copy() # planned row
        adjusted_row = prow.loc[15, ['ddur_1', 'ddur_2', 'ddur_3', 'ddur_4', 'ddur_5', 'ddur_6', 'ddur_7', 'ddur_8']] * R_n
        adjusted_row = adjusted_row.astype(int)
        Rhist.loc[n, ['ddur_1', 'ddur_2', 'ddur_3', 'ddur_4', 'ddur_5', 'ddur_6', 'ddur_7', 'ddur_8']] = adjusted_row.values
        Rhist.loc[n, 'cycle'] = adjusted_row.sum()
        pass

display(Rhist)

inter_no    end_unix  ddur_1  ddur_2  ddur_3  ddur_4  ddur_5  ddur_6  \
0       178  1704460360      38      39      44      36      23       0   
1       178  1704460540      38      39      44      36      23       0   
2       178  1704460720      38      39      44      36      23       0   
3       178  1704460864      38      39      44      36      23       0   
4       178  1704461040      38      39      44      36      23       0   
5       178  1704461219      38      39      44      36      23       0   

   ddur_7  ddur_8  cycle  offset  diff  
0       0       0    180      75     0  
1       0       0    180      75   180  
2       0       0    180      75   180  
3       0       0    180      75   144  
4       0       0    180      75   176  
5       0       0    180      75   179

1.0
1704460360
1704458740
1620
1620
0
1.0
1704460540
1704458740
1800
1800
0
0.8
1704460720
1704458740
1980
1980
0
0.9777777777777777
1704460864
1704458740
2124
2160
-36
0.9944444444444445
1704461040
1704458740
2300
2340
-40


inter_no    end_unix  ddur_1  ddur_2  ddur_3  ddur_4  ddur_5  ddur_6  \
0       178  1704460360      38      39      44      36      23       0   
1       178  1704460540      38      39      44      36      23       0   
2       178  1704460720      38      39      44      36      23       0   
3       178  1704460864      37      38      43      35      22       0   
4       178  1704461040      37      38      43      35      22       0   
5       178  1704461219      38      39      44      36      23       0   

   ddur_7  ddur_8  cycle  offset  
0       0       0    180      75  
1       0       0    180      75  
2       0       0    180      75  
3       0       0    175      75  
4       0       0    175      75  
5       0       0    180      75

In [257]:
rhist_diff = rhist.copy()
rhist_diff['diff'] = rhist_diff['end_unix'].diff().fillna(0).astype(int)
# display(rhist_diff) # 이상치 처리 전
end_unixes = rhist.end_unix.unique()
n = 0
curr_unix = rhist.iloc[n].end_unix # current end_unix
print(curr_unix)
ghour_lt_end_unix = hours[hours < curr_unix].max() # the greatest hour less than curr_unix
print(ghour_lt_end_unix)
end_unixes_lt_ghour = np.sort(end_unixes[end_unixes < ghour_lt_end_unix]) # end unixes less than ghour_lt_end_unix
print(end_unixes_lt_ghour)
base_unix = end_unixes_lt_ghour[-5] # 기준유닉스 : curr_unix보다 작은 hour 중에서 가장 큰 값으로부터 다섯 번째로 작은 end_unix
print(base_unix)

1704454239
1704452400
[]


IndexError: index -5 is out of bounds for axis 0 with size 0

In [176]:
fmins = range(midnight, next_day, 300) # fmins : unix time by Five MINuteS
m = 280 # ranges from 0 to 287, but 0 makes an error where 288 = 86400//300
present_time = fmins[m] # 현재시점
# - 5분마다 신호이력 데이터 수집해서 통합테이블 생성할때
# 1. 조회시점의 유닉스 타임을 기준으로 신호이력의 유닉스 타임이 2시간 이내인 데이터 수집
rhistory = history.copy() # recent history 1704393231
rhistory = rhistory[(rhistory.end_unix < present_time) & (rhistory.end_unix >= present_time - 7200)]
hours = np.array(range(midnight, next_day + 1, 3600))
rhist = rhistory.copy()[rhistory.inter_no == 178]
hist = history.copy()[history.inter_no == 178]
end_unixes = rhist.end_unix.unique()
rhist_diff = rhist.copy()
rhist_diff['diff'] = rhist_diff['end_unix'].diff().fillna(0).astype(int)
display(rhist_diff) # 결측치 처리 전
rhist = rhist.reset_index(drop=True)
new_rows = []
# 1-1. 결측치 처리 : 인접한 두 end_unix의 차이가 계획된 주기의 두 배보다 크면 결측이 일어났다고 판단
for n in range(len(rhist) - 1):
    curr_unix = rhist.iloc[n].end_unix # current end_unix
    next_unix = rhist.iloc[n+1].end_unix # next end_unix
    cycle = rhist.iloc[n].cycle
    start_seconds = np.array(timetable.start_seconds)
    idx = (start_seconds <= 1704396909).sum() - 1
    start_hour = timetable.iloc[idx].start_hour
    start_minute = timetable.iloc[idx].start_minute
    if next_unix - curr_unix >= 2 * cycle:
        # 현재 unix를 계획된 주기만큼 늘려가면서 한 행씩 채워나간다.
        #(다음 unix와의 차이가 계획된 주기보다 작거나 같아질 때까지)
        while next_unix - curr_unix > cycle:
            curr_unix += cycle
            # print(curr_unix)
            prow = pland[(pland.inter_no==175) & (pland.start_hour==start_hour) & (pland.start_minute==start_minute)] # planned row
            prow = prow.drop(['start_hour', 'start_minute'], axis=1)
            prow['end_unix'] = curr_unix
            display(prow)
            new_rows.append(prow)

rhist = pd.concat([rhist] + new_rows).sort_values(['end_unix'])
rhist_diff = rhist.copy()
rhist_diff['diff'] = rhist_diff['end_unix'].diff().fillna(0).astype(int)
display(rhist_diff) # 결측치 처리 후
rhist = rhist.reset_index(drop=True)
rhist

inter_no    end_unix  ddur_1  ddur_2  ddur_3  ddur_4  ddur_5  ddur_6  \
4375       178  1704457300      38      39      44      36      23       0   
4384       178  1704457480      38      39      44      36      23       0   
4394       178  1704457660      38      39      44      36      23       0   
4403       178  1704457840      38      39      44      36      23       0   
4411       178  1704458020      38      39      44      36      23       0   
4420       178  1704458201      38      39      44      36      23       0   
4431       178  1704458380      38      39      44      36      23       0   
4441       178  1704458560      38      39      44      36      23       0   
4450       178  1704458740      38      39      44      36      23       0   
4460       178  1704458920      38      39      44      36      23       0   
4468       178  1704459100      38      39      44      36      23       0   
4477       178  1704459280      38      39      44      36      23       0   
4487       178  1704459460      38      39      44      36      23       0   
4497       178  1704459640      38      39      44      36      23       0   
4506       178  1704459820      38      39      44      36      23       0   
4516       178  1704460000      38      39      44      36      23       0   
4526       178  1704460180      38      39      44      36      23       0   
4533       178  1704460360      38      39      44      36      23       0   
4559       178  1704460864      38      39      44      36      23       0   
4569       178  1704461040      38      39      44      36      23       0   
4577       178  1704461219      38      39      44      36      23       0   
4586       178  1704461400      38      39      44      36      23       0   
4597       178  1704461579      38      39      44      36      23       0   
4606       178  1704461760      38      39      44      36      23       0   
4615       178  1704461939      38      39      44      36      23       0   
4625       178  1704462120      38      39      44      36      23       0   
4635       178  1704462300      38      39      44      36      23       0   
4644       178  1704462480      38      39      44      36      23       0   
4653       178  1704462660      38      39      44      36      23       0   
4663       178  1704462840      38      39      44      36      23       0   
4674       178  1704463021      38      39      44      36      23       0   
4681       178  1704463200      38      39      44      36      23       0   
4690       178  1704463381      38      39      44      36      23       0   
4700       178  1704463560      38      39      44      36      23       0   
4709       178  1704463741      38      39      44      36      23       0   
4717       178  1704463920      38      39      44      36      23       0   
4726       178  1704464100      38      39      44      36      23       0   
4737       178  1704464280      38      39      44      36      23       0   

      ddur_7  ddur_8  cycle  offset  diff  
4375       0       0    180      75     0  
4384       0       0    180      75   180  
4394       0       0    180      75   180  
4403       0       0    180      75   180  
4411       0       0    180      75   180  
4420       0       0    180      75   181  
4431       0       0    180      75   179  
4441       0       0    180      75   180  
4450       0       0    180      75   180  
4460       0       0    180      75   180  
4468       0       0    180      75   180  
4477       0       0    180      75   180  
4487       0       0    180      75   180  
4497       0       0    180      75   180  
4506       0       0    180      75   180  
4516       0       0    180      75   180  
4526       0       0    180      75   180  
4533       0       0    180      75   180  
4559       0       0    180      75   504  
4569       0       0    180      75   176  
4577       0       0    180      75   1

inter_no  ddur_1  ddur_2  ddur_3  ddur_4  ddur_5  ddur_6  ddur_7  ddur_8  \
0       175      37      39      25      30      29       0       0       0   

   cycle  offset    end_unix  
0    160      57  1704460540

inter_no  ddur_1  ddur_2  ddur_3  ddur_4  ddur_5  ddur_6  ddur_7  ddur_8  \
0       175      37      39      25      30      29       0       0       0   

   cycle  offset    end_unix  
0    160      57  1704460720

inter_no    end_unix  ddur_1  ddur_2  ddur_3  ddur_4  ddur_5  ddur_6  \
0        178  1704457300      38      39      44      36      23       0   
1        178  1704457480      38      39      44      36      23       0   
2        178  1704457660      38      39      44      36      23       0   
3        178  1704457840      38      39      44      36      23       0   
4        178  1704458020      38      39      44      36      23       0   
5        178  1704458201      38      39      44      36      23       0   
6        178  1704458380      38      39      44      36      23       0   
7        178  1704458560      38      39      44      36      23       0   
8        178  1704458740      38      39      44      36      23       0   
9        178  1704458920      38      39      44      36      23       0   
10       178  1704459100      38      39      44      36      23       0   
11       178  1704459280      38      39      44      36      23       0   
12       178  1704459460      38      39      44      36      23       0   
13       178  1704459640      38      39      44      36      23       0   
14       178  1704459820      38      39      44      36      23       0   
15       178  1704460000      38      39      44      36      23       0   
16       178  1704460180      38      39      44      36      23       0   
17       178  1704460360      38      39      44      36      23       0   
0        175  1704460540      37      39      25      30      29       0   
0        175  1704460720      37      39      25      30      29       0   
18       178  1704460864      38      39      44      36      23       0   
19       178  1704461040      38      39      44      36      23       0   
20       178  1704461219      38      39      44      36      23       0   
21       178  1704461400      38      39      44      36      23       0   
22       178  1704461579      38      39      44      36      23       0   
23       178  1704461760      38      39      44      36      23       0   
24       178  1704461939      38      39      44      36      23       0   
25       178  1704462120      38      39      44      36      23       0   
26       178  1704462300      38      39      44      36      23       0   
27       178  1704462480      38      39      44      36      23       0   
28       178  1704462660      38      39      44      36      23       0   
29       178  1704462840      38      39      44      36      23       0   
30       178  1704463021      38      39      44      36      23       0   
31       178  1704463200      38      39      44      36      23       0   
32       178  1704463381      38      39      44      36      23       0   
33       178  1704463560      38      39      44      36      23       0   
34       178  1704463741      38      39      44      36      23       0   
35       178  1704463920      38      39      44      36      23       0   
36       178  1704464100      38      39      44      36      23       0   
37       178  1704464280      38      39      44      36      23       0   

    ddur_7  ddur_8  cycle  offset  diff  
0        0       0    180      75     0  
1        0       0    180      75   180  
2        0       0    180      75   180  
3        0       0    180      75   180  
4        0       0    180      75   180  
5        0       0    180      75   181  
6        0       0    180      75   179  
7        0       0    180      75   180  
8        0       0    180      75   180  
9        0       0    180      75   180  
10       0       0    180      75   180  
11       0       0    180      75   180  
12       0       0    180      75   180  
13       0       0    180      75   180  
14       0       0    180      75   180  
15       0       0    180      75   180  
16       0       0    180      75   180  
17       0       0    180      75   180  
0        0       0    160      57   180  
0        0       0    160      57   180  
18   

inter_no    end_unix  ddur_1  ddur_2  ddur_3  ddur_4  ddur_5  ddur_6  \
0        178  1704457300      38      39      44      36      23       0   
1        178  1704457480      38      39      44      36      23       0   
2        178  1704457660      38      39      44      36      23       0   
3        178  1704457840      38      39      44      36      23       0   
4        178  1704458020      38      39      44      36      23       0   
5        178  1704458201      38      39      44      36      23       0   
6        178  1704458380      38      39      44      36      23       0   
7        178  1704458560      38      39      44      36      23       0   
8        178  1704458740      38      39      44      36      23       0   
9        178  1704458920      38      39      44      36      23       0   
10       178  1704459100      38      39      44      36      23       0   
11       178  1704459280      38      39      44      36      23       0   
12       178  1704459460      38      39      44      36      23       0   
13       178  1704459640      38      39      44      36      23       0   
14       178  1704459820      38      39      44      36      23       0   
15       178  1704460000      38      39      44      36      23       0   
16       178  1704460180      38      39      44      36      23       0   
17       178  1704460360      38      39      44      36      23       0   
18       175  1704460540      37      39      25      30      29       0   
19       175  1704460720      37      39      25      30      29       0   
20       178  1704460864      38      39      44      36      23       0   
21       178  1704461040      38      39      44      36      23       0   
22       178  1704461219      38      39      44      36      23       0   
23       178  1704461400      38      39      44      36      23       0   
24       178  1704461579      38      39      44      36      23       0   
25       178  1704461760      38      39      44      36      23       0   
26       178  1704461939      38      39      44      36      23       0   
27       178  1704462120      38      39      44      36      23       0   
28       178  1704462300      38      39      44      36      23       0   
29       178  1704462480      38      39      44      36      23       0   
30       178  1704462660      38      39      44      36      23       0   
31       178  1704462840      38      39      44      36      23       0   
32       178  1704463021      38      39      44      36      23       0   
33       178  1704463200      38      39      44      36      23       0   
34       178  1704463381      38      39      44      36      23       0   
35       178  1704463560      38      39      44      36      23       0   
36       178  1704463741      38      39      44      36      23       0   
37       178  1704463920      38      39      44      36      23       0   
38       178  1704464100      38      39      44      36      23       0   
39       178  1704464280      38      39      44      36      23       0   

    ddur_7  ddur_8  cycle  offset  
0        0       0    180      75  
1        0       0    180      75  
2        0       0    180      75  
3        0       0    180      75  
4        0       0    180      75  
5        0       0    180      75  
6        0       0    180      75  
7        0       0    180      75  
8        0       0    180      75  
9        0       0    180      75  
10       0       0    180      75  
11       0       0    180      75  
12       0       0    180      75  
13       0       0    180      75  
14       0       0    180      75  
15       0       0    180      75  
16       0       0    180      75  
17       0       0    180      75  
18       0       0    160      57  
19       0       0    160      57  
20       0       0    180      75  
21       0       0    180      75  
22       0       0    180      75  
23       0       0    1

In [169]:
# 1704460864
fmins = range(midnight, next_day, 300) # fmins : unix time by Five MINuteS
m = 280 # ranges from 0 to 287, but 0 makes an error where 288 = 86400//300
present_time = fmins[m] # 현재시점
# - 5분마다 신호이력 데이터 수집해서 통합테이블 생성할때
# 1. 조회시점의 유닉스 타임을 기준으로 신호이력의 유닉스 타임이 2시간 이내인 데이터 수집
rhistory = history.copy() # recent history 1704393231
rhistory = rhistory[(rhistory.end_unix < present_time) & (rhistory.end_unix >= present_time - 7200)]
hours = np.array(range(midnight, next_day + 1, 3600))
rhist = rhistory.copy()[rhistory.inter_no == 178]
hist = history.copy()[history.inter_no == 178]
end_unixes = rhist.end_unix.unique()
rhist_diff = rhist.copy()
rhist_diff['diff'] = rhist_diff['end_unix'].diff().fillna(0).astype(int)
# display(rhist_diff.reset_index(drop=True))
# display(rhist_diff)
rhist = rhist.reset_index(drop=True)
new_rows = []
# n = 16 : 정상
# n = 17 : 비정상
n = 17
curr_unix = rhist.iloc[n].end_unix # current end_unix
next_unix = rhist.iloc[n+1].end_unix # next end_unix
cycle = rhist.iloc[n].cycle
start_seconds = np.array(timetable.start_seconds)
idx = (start_seconds <= 1704396909).sum() - 1
start_hour = timetable.iloc[idx].start_hour
start_minute = timetable.iloc[idx].start_minute
# 1-1. 결측치 처리 : 인접한 두 end_unix의 차이가 계획된 주기의 두 배보다 크면 결측이 일어났다고 판단
if next_unix - curr_unix >= 2 * cycle:
    # 현재 unix를 계획된 주기만큼 늘려가면서 한 행씩 채워나간다.
    #(다음 unix와의 차이가 계획된 주기보다 작거나 같아질 때까지)
    while next_unix - curr_unix > cycle:
        curr_unix += cycle
        # print(curr_unix)
        prow = pland[(pland.inter_no==175) & (pland.start_hour==start_hour) & (pland.start_minute==start_minute)] # planned row
        prow = prow.drop(['start_hour', 'start_minute'], axis=1)
        prow['end_unix'] = curr_unix
        display(prow)
        new_rows.append(prow)
# 1-2. 이상치 처리 : D_n(시간차이)과 S_n(현시시간합)의 차이가 10보다 크면 이상치가 발생했다고 판단
ghour_lt_end_unix = hours[hours < curr_unix].max() # the greatest hour less than curr_unix
end_unixes_lt_ghour = np.sort(end_unixes[end_unixes < ghour_lt_end_unix]) # end unixes less than ghour_lt_end_unix
base_unix = end_unixes_lt_ghour[-5] # 기준유닉스 : curr_unix보다 작은 hour 중에서 가장 큰 값으로부터 다섯 번째로 작은 end_unix
# D_n : 시간차이
D_n = curr_unix - base_unix
print(f"curr_unix:{curr_unix}")
print(datetime.fromtimestamp(ghour_lt_end_unix))
print(f"ghour_lt_end_unix:{ghour_lt_end_unix}")
print(f"base_unix:{base_unix}")
print(D_n)
display(history[history.end_unix==base_unix])
# display(hist[495:]) # max 538
# display(hist[(hist.end_unix >= base_unix) & (hist.end_unix <= curr_unix)])
display(rhist[(rhist.end_unix >= base_unix)])# & (rhist.end_unix <= curr_unix)])
# datetime.utcfromtimestamp(unix_timestamp)

rhist = pd.concat([rhist] + new_rows).sort_values(['end_unix'])
rhist_diff = rhist.copy()
rhist_diff['diff'] = rhist_diff['end_unix'].diff().fillna(0).astype(int)
display(rhist_diff)

inter_no  ddur_1  ddur_2  ddur_3  ddur_4  ddur_5  ddur_6  ddur_7  ddur_8  \
0       175      37      39      25      30      29       0       0       0   

   cycle  offset    end_unix  
0    160      57  1704460540

inter_no  ddur_1  ddur_2  ddur_3  ddur_4  ddur_5  ddur_6  ddur_7  ddur_8  \
0       175      37      39      25      30      29       0       0       0   

   cycle  offset    end_unix  
0    160      57  1704460720

curr_unix:1704460720
2024-01-05 22:00:00
ghour_lt_end_unix:1704459600
base_unix:1704458740
1980


inter_no    end_unix  ddur_1  ddur_2  ddur_3  ddur_4  ddur_5  ddur_6  \
4450       178  1704458740      38      39      44      36      23       0   

      ddur_7  ddur_8  cycle  offset  
4450       0       0    180      75

inter_no    end_unix  ddur_1  ddur_2  ddur_3  ddur_4  ddur_5  ddur_6  \
8        178  1704458740      38      39      44      36      23       0   
9        178  1704458920      38      39      44      36      23       0   
10       178  1704459100      38      39      44      36      23       0   
11       178  1704459280      38      39      44      36      23       0   
12       178  1704459460      38      39      44      36      23       0   
13       178  1704459640      38      39      44      36      23       0   
14       178  1704459820      38      39      44      36      23       0   
15       178  1704460000      38      39      44      36      23       0   
16       178  1704460180      38      39      44      36      23       0   
17       178  1704460360      38      39      44      36      23       0   
18       178  1704460864      38      39      44      36      23       0   
19       178  1704461040      38      39      44      36      23       0   
20       178  1704461219      38      39      44      36      23       0   
21       178  1704461400      38      39      44      36      23       0   
22       178  1704461579      38      39      44      36      23       0   
23       178  1704461760      38      39      44      36      23       0   
24       178  1704461939      38      39      44      36      23       0   
25       178  1704462120      38      39      44      36      23       0   
26       178  1704462300      38      39      44      36      23       0   
27       178  1704462480      38      39      44      36      23       0   
28       178  1704462660      38      39      44      36      23       0   
29       178  1704462840      38      39      44      36      23       0   
30       178  1704463021      38      39      44      36      23       0   
31       178  1704463200      38      39      44      36      23       0   
32       178  1704463381      38      39      44      36      23       0   
33       178  1704463560      38      39      44      36      23       0   
34       178  1704463741      38      39      44      36      23       0   
35       178  1704463920      38      39      44      36      23       0   
36       178  1704464100      38      39      44      36      23       0   
37       178  1704464280      38      39      44      36      23       0   

    ddur_7  ddur_8  cycle  offset  
8        0       0    180      75  
9        0       0    180      75  
10       0       0    180      75  
11       0       0    180      75  
12       0       0    180      75  
13       0       0    180      75  
14       0       0    180      75  
15       0       0    180      75  
16       0       0    180      75  
17       0       0    180      75  
18       0       0    180      75  
19       0       0    180      75  
20       0       0    180      75  
21       0       0    180      75  
22       0       0    180      75  
23       0       0    180      75  
24       0       0    180      75  
25       0       0    180      75  
26       0       0    180      75  
27       0       0    180      75  
28       0       0    180      75  
29       0       0    180      75  
30       0       0    180      75  
31       0       0    180      75  
32       0       0    180      75  
33       0       0    180      75  
34       0       0    180      75  
35       0       0    180      75  
36       0       0    180      75  
37       0       0    180      75

inter_no    end_unix  ddur_1  ddur_2  ddur_3  ddur_4  ddur_5  ddur_6  \
0        178  1704457300      38      39      44      36      23       0   
1        178  1704457480      38      39      44      36      23       0   
2        178  1704457660      38      39      44      36      23       0   
3        178  1704457840      38      39      44      36      23       0   
4        178  1704458020      38      39      44      36      23       0   
5        178  1704458201      38      39      44      36      23       0   
6        178  1704458380      38      39      44      36      23       0   
7        178  1704458560      38      39      44      36      23       0   
8        178  1704458740      38      39      44      36      23       0   
9        178  1704458920      38      39      44      36      23       0   
10       178  1704459100      38      39      44      36      23       0   
11       178  1704459280      38      39      44      36      23       0   
12       178  1704459460      38      39      44      36      23       0   
13       178  1704459640      38      39      44      36      23       0   
14       178  1704459820      38      39      44      36      23       0   
15       178  1704460000      38      39      44      36      23       0   
16       178  1704460180      38      39      44      36      23       0   
17       178  1704460360      38      39      44      36      23       0   
0        175  1704460540      37      39      25      30      29       0   
0        175  1704460720      37      39      25      30      29       0   
18       178  1704460864      38      39      44      36      23       0   
19       178  1704461040      38      39      44      36      23       0   
20       178  1704461219      38      39      44      36      23       0   
21       178  1704461400      38      39      44      36      23       0   
22       178  1704461579      38      39      44      36      23       0   
23       178  1704461760      38      39      44      36      23       0   
24       178  1704461939      38      39      44      36      23       0   
25       178  1704462120      38      39      44      36      23       0   
26       178  1704462300      38      39      44      36      23       0   
27       178  1704462480      38      39      44      36      23       0   
28       178  1704462660      38      39      44      36      23       0   
29       178  1704462840      38      39      44      36      23       0   
30       178  1704463021      38      39      44      36      23       0   
31       178  1704463200      38      39      44      36      23       0   
32       178  1704463381      38      39      44      36      23       0   
33       178  1704463560      38      39      44      36      23       0   
34       178  1704463741      38      39      44      36      23       0   
35       178  1704463920      38      39      44      36      23       0   
36       178  1704464100      38      39      44      36      23       0   
37       178  1704464280      38      39      44      36      23       0   

    ddur_7  ddur_8  cycle  offset  diff  
0        0       0    180      75     0  
1        0       0    180      75   180  
2        0       0    180      75   180  
3        0       0    180      75   180  
4        0       0    180      75   180  
5        0       0    180      75   181  
6        0       0    180      75   179  
7        0       0    180      75   180  
8        0       0    180      75   180  
9        0       0    180      75   180  
10       0       0    180      75   180  
11       0       0    180      75   180  
12       0       0    180      75   180  
13       0       0    180      75   180  
14       0       0    180      75   180  
15       0       0    180      75   180  
16       0       0    180      75   180  
17       0       0    180      75   180  
0        0       0    160      57   180  
0        0       0    160      57   180  
18   

In [110]:
fmins = range(midnight, next_day, 300) # fmins : unix time by Five MINuteS
m = 60 # ranges from 0 to 287, but 0 makes an error where 288 = 86400//300
present_time = fmins[m] # 현재시점
# - 5분마다 신호이력 데이터 수집해서 통합테이블 생성할때
# 1. 조회시점의 유닉스 타임을 기준으로 신호이력의 유닉스 타임이 2시간 이내인 데이터 수집
rhistory = history.copy() # recent history 1704393231
rhistory = rhistory[(rhistory.end_unix < present_time) & (rhistory.end_unix >= present_time - 7200)]
end_unixes = rhistory.end_unix.unique()
hours = np.array(range(midnight, next_day + 1, 3600))
rhist = rhistory.copy()[rhistory.inter_no == 175]
rhist_diff = rhist.copy()
rhist_diff['diff'] = rhist_diff['end_unix'].diff().fillna(0).astype(int)
display(rhist_diff)
rhist = rhist.reset_index(drop=True)
new_rows = []
for n in range(len(rhist) - 1):
    curr_unix = rhist.iloc[n].end_unix # current end_unix
    next_unix = rhist.iloc[n+1].end_unix # next end_unix
    cycle = rhist.iloc[n].cycle
    start_seconds = np.array(timetable.start_seconds)
    idx = (start_seconds <= 1704396909).sum() - 1
    start_hour = timetable.iloc[idx].start_hour
    start_minute = timetable.iloc[idx].start_minute
    # 1-1. 결측치 처리 : 인접한 두 end_unix의 차이가 계획된 주기의 두 배보다 크면 결측이 일어났다고 판단
    if next_unix - curr_unix >= 2 * cycle:
        # 현재 unix를 계획된 주기만큼 늘려가면서 한 행씩 채워나간다.
        #(다음 unix와의 차이가 계획된 주기보다 작거나 같아질 때까지)
        while next_unix - curr_unix > cycle:
            curr_unix += cycle
            # print(curr_unix)
            prow = pland[(pland.inter_no==175) & (pland.start_hour==start_hour) & (pland.start_minute==start_minute)] # planned row
            prow = prow.drop(['start_hour', 'start_minute'], axis=1)
            prow['end_unix'] = curr_unix
            display(prow)
            new_rows.append(prow)
    # 1-2. 이상치 처리 : D_n(시간차이)과 S_n(현시시간합)의 차이가 10보다 크면 이상치가 발생했다고 판단
    ghour_lt_end_unix = hours[hours < curr_unix].max() # the greatest hour less than end_unix
    end_unixes_lt_ghour = np.sort(end_unixes[end_unixes < ghour_lt_end_unix]) # end unixes less than ghour_lt_end_unix
    base_unix = end_unixes_lt_ghour[-5] # 기준유닉스 : curr_unix보다 작은 hour 중에서 가장 큰 값으로부터 다섯 번째로 작은 end_unix
    # D_n : 시간차이
    D_n = curr_unix - base_unix

rhist = pd.concat([rhist] + new_rows).sort_values(['end_unix'])
rhist_diff = rhist.copy()
rhist_diff['diff'] = rhist_diff['end_unix'].diff().fillna(0).astype(int)
display(rhist_diff)

inter_no    end_unix  ddur_1  ddur_2  ddur_3  ddur_4  ddur_5  ddur_6  \
693        175  1704391210      37      39      25      30      29       0   
702        175  1704391370      37      39      25      30      29       0   
712        175  1704391530      37      39      25      30      29       0   
723        175  1704391690      37      39      25      30      29       0   
732        175  1704391850      37      39      25      30      29       0   
741        175  1704392010      37      39      25      30      29       0   
755        175  1704392170      37      39      25      30      29       0   
764        175  1704392330      37      39      25      30      29       0   
773        175  1704392490      37      39      25      30      29       0   
784        175  1704392651      37      39      25      30      29       0   
793        175  1704392810      37      39      25      30      29       0   
802        175  1704392970      37      39      25      30      29       0   
813        175  1704393130      37      39      25      30      29       0   
825        175  1704393290      37      39      25      30      29       0   
834        175  1704393450      37      39      25      30      29       0   
846        175  1704393610      37      39      25      30      29       0   
856        175  1704393770      37      39      25      30      29       0   
865        175  1704393930      37      39      25      30      29       0   
876        175  1704394090      37      39      25      30      29       0   
886        175  1704394250      37      39      25      30      29       0   
898        175  1704394410      37      39      25      30      29       0   
909        175  1704394570      37      39      25      30      29       0   
918        175  1704394730      37      39      25      30      29       0   
927        175  1704394890      37      39      25      30      29       0   
938        175  1704395050      37      39      25      30      29       0   
947        175  1704395210      37      39      25      30      29       0   
956        175  1704395370      37      39      25      30      29       0   
970        175  1704395530      37      39      25      30      29       0   
979        175  1704395690      37      39      25      30      29       0   
988        175  1704395850      37      39      25      30      29       0   
999        175  1704396010      37      39      25      30      29       0   
1009       175  1704396170      37      39      25      30      29       0   
1018       175  1704396330      37      39      25      30      29       0   
1030       175  1704396490      37      39      25      30      29       0   
1042       175  1704396650      37      39      25      30      29       0   
1052       175  1704396810      37      39      25      30      29       0   
1063       175  1704396970      37      39      25      30      29       0   
1072       175  1704397130      37      39      25      30      29       0   
1081       175  1704397290      37      39      25      30      29       0   
1093       175  1704397451      37      39      25      30      29       0   
1102       175  1704397610      37      39      25      30      29       0   
1113       175  1704397770      37      39      25      30      29       0   
1124       175  1704397930      37      39      25      30      29       0   
1134       175  1704398089      37      39      25      30      29       0   
1142       175  1704398250      37      39      25      30      29       0   

      ddur_7  ddur_8  cycle  offset  diff  
693        0       0    160      57     0  
702        0       0    160      57   160  
712        0       0    160      57   160  
723        0       0    160      57   160  
732        0       0    160      57   160  
741        0       0    160      57   160  
755        0       0    160      57   160  
764        0       0    160      57   160  
773        0       0 

IndexError: index -5 is out of bounds for axis 0 with size 0

In [ ]:
print(present_time)
print(midnight)
print(rhistory.end_unix.max() - rhistory.end_unix.min())

In [ ]:
import numpy as np

# 주어진 배열
A = np.array([1, 3, 2, 5, 7])

# 배열이 정렬되었는지 확인하는 간단한 방법
is_sorted = np.sort(A) is A

is_sorted


In [ ]:
L = np.array([1,4,6,10,14,25,31,38])
L[-4]

In [ ]:
end_unixes = rhistory.end_unix.unique()
end_unix = end_unixes[300] # 0 ~ 338
ghour_lt_end_unix = hours[hours < end_unix].max() # the greatest hour less than end_unix
end_unixes_lt_ghour = np.sort(end_unixes[end_unixes < ghour_lt_end_unix]) # end unixes less than ghour_lt_end_unix
base_unix = end_unixes_lt_ghour[-5]
D_n = end_unix - base_unix
print(f'D_n : {D_n}')
print(base_unix)
print(end_unix)
print(hours)
S_n = rhistory.loc[(rhistory.end_unix > base_unix) & (rhistory.end_unix <= end_unix)][[f'ddur_{j}' for j in range(1,9)]].values.shape#sum()
print(S_n)
# 이 두 값이 같아야 하는데 같지 않다. 2024. 1. 12 금 : 퇴근하면서

In [ ]:
rhistory

In [ ]:
# 세부현시로 되어있던 history를 A, B로 나뉘어 현시시간이 구성된 형태로 바꿈.
plan = pd.read_csv('../../Data/tables/plan.csv', index_col=0)
history = pd.read_csv('../../Data/tables/history.csv', index_col=0)

# A, B 분리 혹은 통합시 사용할 수 있는 딕셔너리
splits = {} # splits maps (inter_no, start_hour, start_minute) to split
for i, row in plan.iterrows():
    inter_no = row.inter_no
    start_hour = row.start_hour
    start_minute = row.start_minute
    cycle = row.cycle
    cums_A = row[[f'dura_A{j}' for j in range(1,9)]].cumsum()
    cums_B = row[[f'dura_B{j}' for j in range(1,9)]].cumsum()
    splits[(inter_no, start_hour, start_minute)] = {} # split maps (phas_A, phas_B) to k
    k = 0
    for t in range(cycle):
        new_phas_A = len(cums_A[cums_A < t]) + 1
        new_phas_B = len(cums_B[cums_B < t]) + 1
        if k == 0 or ((new_phas_A, new_phas_B) != (phas_A, phas_B)):
            k += 1
        phas_A = new_phas_A
        phas_B = new_phas_B
        splits[(inter_no, start_hour, start_minute)][(phas_A, phas_B)] = k
# the inverse of splits
isplits = {} # isplit maps k to (phas_A, phas_B)
for i in splits:
    isplits[i] = {splits[i][k]:k for k in splits[i]}

timetable = plan[['start_hour', 'start_minute']].drop_duplicates()
timetable['start_seconds'] = midnight + timetable['start_hour'] * 3600 + timetable['start_minute'] * 60

abhistory = history.copy() # A, B가 나뉘어진 history
# history의 행들을 순회하며 새로운 열 dur_A1, dur_A2, ... 를 만들어내고 값을 배정함.
for i, row in abhistory.iterrows():
    inter_no = row.inter_no
    ind = (timetable['start_seconds'] < row.end_unix).sum() - 1
    start_hour = timetable.iloc[ind].start_hour
    start_minute = timetable.iloc[ind].start_minute
    isplit = isplits[(inter_no,start_hour,start_minute)]
    dur_dict = {}
    dur_chars = [f'dur_{alph}{j}' for alph in ['A', 'B'] for j in range(1, 9)] # 새로운 행들
    for dur_char in dur_chars:
        dur_dict[dur_char] = 0
    for k in range(1, len(isplit)+1): # dur_dict에 값 저장
        ja = isplit[k][0] # A현시번호
        jb = isplit[k][1] # B현시번호
        dur_dict[f'dur_A{ja}'] += row[f'ddur_{k}']
        dur_dict[f'dur_B{jb}'] += row[f'ddur_{k}']
    for dur_char in dur_chars: # history의 새로운 열들에 값 배정
        abhistory.at[i, dur_char] = dur_dict[dur_char]
abhistory = abhistory[['inter_no','end_unix'] + dur_chars + ['cycle']].astype(int)
abhistory = abhistory.astype(int).sort_values(by = ['end_unix','inter_no'])
abhistory.head()

In [ ]:
fmins = range(midnight, next_day, 300) # fmins : unix time by Five MINuteS

def make_histid(m:int):
    '''
    input : m
     - m ranges from 0 to 287, but 0 makes an error where 288 = 86400//300
     - present_time = fmins[m] : 현재시점
    output : histid
     - history with edge ids (incoming and outgoing edge ids)
     - 현재시점으로부터 한시간동안 (교차로번호, 현시, 링)별 현시시간, 진입엣지id, 진출엣지id
    '''
    present_time = fmins[m] ####### 현재 시점 ranges from 0 to 287
    # - 5분마다 신호이력 데이터 수집해서 통합테이블 생성할때
    # 1. 조회시점의 유닉스 타임을 기준으로 신호이력의 유닉스 타임이 1시간 이내인 데이터 수집
    rhistory = history.copy()
    rhistory = rhistory[(rhistory.end_unix < present_time) & (rhistory.end_unix >= present_time - 3600)]
    ddurs = [f'ddur_{j}' for j in range(1, 9)]

    # 2. 시작 유닉스 타임컬럼 생성 후 종류 유닉스 타임에서 현시별 현시기간 컬럼의 합을 뺀 값으로 입력
    # - 현시시간의 합을 뺀 시간의 +- 10초 이내에 이전 주기정보가 존재하면 그 유닉스 시간을 시작 유닉스시간 값으로 하고, 존재하지 않으면 현시시간의 합을 뺀 유닉스 시간을 시작 유닉스 시간으로 지정
    # # 이전 유닉스 존재하지 않음 => 현시시간 합의 차
    # # 이전 유닉스 존재, abs < 10 => 이전 유닉스
    # # 이전 유닉스 존재, abs >=10 => 현시시간 합의 차
    for i, row in rhistory.iterrows():
        inter_no = row.inter_no
        end_unix = row.end_unix
        elapsed_time = row[ddurs].sum()
        start_unix = end_unix - elapsed_time
        pre_rows = history[:i] # previous rows
        if inter_no in pre_rows.inter_no.unique(): # 이전 유닉스 존재
            pre_unix = pre_rows[pre_rows.inter_no == inter_no]['end_unix'].iloc[-1] # previous unix time
            if abs(pre_unix - start_unix) < 10: # abs < 10
                start_unix = pre_unix
            else: # abs >= 10
                pass
        rhistory.loc[i, 'start_unix'] = start_unix
    rhistory[rhistory.isna()] = 0
    rhistory['start_unix'] = rhistory['start_unix'].astype(int)
    # with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    #     display(rhistory)
    rhistory = rhistory[['inter_no', 'start_unix'] + ddurs + ['cycle']]

    # 계층화된 형태로 변환
    hrhistory = [] # hierarchied recent history
    for i, row in rhistory.iterrows():
        inter_no = row.inter_no #
        start_unix = row.start_unix #
        ind = (timetable['start_seconds'] <= row.start_unix).sum() - 1
        start_hour = timetable.iloc[ind].start_hour
        start_minute = timetable.iloc[ind].start_minute
        isplit = isplits[(inter_no, start_hour, start_minute)]
        new_rows = []
        for j in isplit.keys():
            phas_A, phas_B = isplit[j]
            duration = row[f'ddur_{j}']
            new_rows.append(pd.DataFrame({'inter_no':[inter_no], 'start_unix':[start_unix],
                                        'phas_A':[phas_A],'phas_B':[phas_B],'duration':[duration]}))
        new_rows = pd.concat(new_rows)
        hrhistory.append(new_rows)
    hrhistory = pd.concat(hrhistory)
    hrhistory = hrhistory.sort_values(by = ['start_unix', 'inter_no', 'phas_A', 'phas_B']).reset_index(drop=True)

    # 5초단위로 수집한 이동류정보(time2movement[present_time])와 최근 1시간 신호이력(hrhistory)을 병합
    movedur = pd.merge(time2movement[present_time], hrhistory, how='inner', on=['inter_no', 'start_unix', 'phas_A', 'phas_B'])
    # movements and durations
    movedur = movedur.sort_values(by=['start_unix', 'inter_no', 'phas_A','phas_B'])
    movedur = movedur[['inter_no', 'start_unix', 'phas_A', 'phas_B', 'move_A', 'move_B', 'duration']]
    # 이동류 매칭 테이블에서 진입id, 진출id를 가져와서 붙임.
    for i, row in movedur.iterrows():
        inter_no = row.inter_no
        start_unix = row.start_unix
        move_A = row.move_A
        move_B = row.move_B
        match_A = matching[(matching.inter_no == inter_no) & (matching.move_no == move_A)].iloc[0]
        match_B = matching[(matching.inter_no == inter_no) & (matching.move_no == move_B)].iloc[0]
        inc_edge_A = match_A.inc_edge
        inc_edge_B = match_B.inc_edge
        out_edge_A = match_A.out_edge
        out_edge_B = match_B.out_edge
        movedur.loc[i, ['inc_edge_A', 'inc_edge_B', 'out_edge_A', 'out_edge_B']] = [inc_edge_A, inc_edge_B, out_edge_A, out_edge_B]
    # 이동류 컬럼 제거
    movedur = movedur.drop(['move_A', 'move_B'], axis=1)

    histid = movedur.copy() # history with edge ids (incoming and outgoing edge ids)
    return histid

In [ ]:
make_histid(200).inter_no.unique()

In [ ]:
hist = history.copy()[history.inter_no==175]
hist['diff'] = hist['end_unix'].diff()
hist = hist[1:]
hist
hist['diff'] = hist['diff'].astype(int)
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    display(hist)

# 3. 결측, 이상치 처리

In [ ]:
planned = plan.copy()
planned['start_unix'] = planned['start_hour'] * 3600 +planned['start_minute'] * 60 + midnight
start_unixes = planned.start_unix.unique()
planned['pstart_unix'] = planned['start_unix'].apply(lambda x:start_unixes[sum(start_unixes <= x) - 1]) # the unix time when the program started
planned = planned[['inter_no', 'start_unix'] + [f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)] + ['cycle', 'pstart_unix']]
planned.head(10)

In [ ]:
make_histid(100).inter_no.unique()

In [ ]:
pland = plan.copy() # A, B가 통합된 plan (plan detailed)
cums_A = np.array(pland[[f'dura_A{k}' for k in range(1,9)]].cumsum(axis=1))
cums_B = np.array(pland[[f'dura_B{k}' for k in range(1,9)]].cumsum(axis=1))
detailed_cums = []
i = 0
for row_A, row_B in zip(cums_A, cums_B):
    combined_row = np.unique(np.concatenate((row_A, row_B)))
    ddur = np.concatenate(([combined_row[0]], np.diff(combined_row)))
    ddur = np.pad(ddur, (0, 8 - len(ddur)), constant_values=(0))
    detailed_cums.append(ddur)
    for j in range(8):
        pland.at[i, f'ddur_{j+1}'] = ddur[j]
    i+=1
pland = pland[['inter_no', 'start_hour', 'start_minute'] + [f'ddur_{i}' for i in range(1,9)] + ['cycle', 'offset']] # plan detailed
pland[[f'ddur_{i}' for i in range(1,9)]] = pland[[f'ddur_{i}' for i in range(1,9)]].astype(int)
pland[:10]

In [ ]:
histid = make_histid(25)

In [ ]:
inter_no = 175
hist = histid.copy()[histid.inter_no==inter_no]
hist = hist.reset_index(drop=True)
hist['diff'] = hist['start_unix'].diff().fillna(0).astype(int)
hist = hist.set_index('start_unix')
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    display(hist)

In [ ]:
inter_no = 175
hist = histid.copy()[histid.inter_no==inter_no]
hist = hist.reset_index(drop=True)
hist['diff'] = hist['start_unix'].diff().fillna(0).astype(int)
hist = hist.set_index('start_unix')
start_unixes = hist.index.unique()
for n in range(1, len(start_unixes)):
    ind = (timetable['start_seconds'] <= start_unixes[n]).sum() - 1    
    start_hour = timetable.iloc[ind].start_hour
    start_minute = timetable.iloc[ind].start_minute
    prow = pland[(pland.inter_no == inter_no)&(pland.start_hour == start_hour)&(pland.start_minute == start_minute)].iloc[0] # planned row
    cycle = prow.cycle
    if start_unixes[n] - start_unixes[n-1] < 2 * cycle:
        pass
    else:

In [ ]:
hist

In [ ]:
matching

In [ ]:
n = 3
ind = (timetable['start_seconds'] <= start_unixes[n]).sum() - 1    
start_hour = timetable.iloc[ind].start_hour
start_minute = timetable.iloc[ind].start_minute
prow = pland[(pland.inter_no == inter_no)&(pland.start_hour == start_hour)&(pland.start_minute == start_minute)].iloc[0] # planned row
cycle = prow.cycle
print(start_unixes[n] - start_unixes[n-1] < 2 * cycle)
ddurs = [f'ddur_{j}' for j in range(1, 9)]
print(prow[ddurs])
ndphase = (prow[ddurs]!=0).sum() # the number of (detailed) phases
isplit = isplits[(inter_no,start_hour,start_minute)]
print(isplit)
inter_nos = [inter_no] * ndphase
phas_As = [isplit[i][0] for i in isplit.keys()]
phas_Bs = [isplit[i][1] for i in isplit.keys()]
durations = prow[ddurs][prow[ddurs]!=0]
# new_rows = pd.DataFrame()